In [14]:
from google.colab import drive
drive.mount('/content/gdrive')
%cd "/content/gdrive/MyDrive/Colab Notebooks/IT401_Project/"

Drive already mounted at /content/gdrive; to attempt to forcibly remount, call drive.mount("/content/gdrive", force_remount=True).
/content/gdrive/MyDrive/Colab Notebooks/IT401_Project


In [15]:
!pip install keras_preprocessing
# !pip install translate

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [16]:
import numpy as np
import os, sys
import pickle, functools, operator
from tensorflow import keras
from keras.preprocessing.text import Tokenizer
from keras_preprocessing.sequence import pad_sequences
# from keras.preprocessing.sequence import pad_sequences
import joblib
from tensorflow.keras.utils import to_categorical
from keras.models import Model, load_model
from keras.layers import Input, LSTM, Dense
from keras.callbacks import EarlyStopping, ModelCheckpoint
import json
import random
from keras.utils.vis_utils import plot_model
import tensorflow as tf
import datetime

In [17]:
train_path = "Data/training_data"
test_path = "Data/testing_data"
batch_size = 320
learning_rate = 0.0007
epochs = 15
latent_dim = 512
num_encoder_tokens = 4096
num_decoder_tokens = 1500
time_steps_encoder = 80
max_probability = -1
save_model_path = 'model_final'
validation_split = 0.15
max_length = 10
search_type = 'greedy'

In [18]:
sr={'id':'cap'}
sr['id']=3
sr['cap']='Sup'
print(sr['id'])

3


In [19]:
pip install googletrans==3.1.0a0

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [20]:
# print(googletrans.LANGUAGES)
from googletrans import Translator
translator = Translator()

hin_str=translator.translate('A woman goes under a horse', src='en', dest='hi')
print(hin_str.text)

एक महिला घोड़े के नीचे जाती है


In [23]:
from googletrans import Translator
translator = Translator()

hindi_captions=[]
TRAIN_LABEL_PATH = os.path.join('', 'testing_hindi_label.json')
with open(TRAIN_LABEL_PATH) as data_file:    
    y_data = json.load(data_file)
    for i in range(100):
      hindi_captions=[]
      for j in y_data[i]['caption']:
        hindi_captions.append(translator.translate(j,  dest='hi').text)
      y_data[i]['caption']=hindi_captions

In [25]:
y_data

{'caption': ['एक मछली पकड़ने वाला एक लड़के का पीछा कर रहा है।',
  'एक छोटा बच्चा अपने हाथ में पकड़ी हुई छड़ी पर मछली से बचने की कोशिश में घेरे में इधर-उधर दौड़ रहा है, तभी वह पोल को गिरा देता है और भाग जाता है।',
  'एक छोटा बच्चा मछली पकड़ने के खंभे के चारों ओर दौड़ रहा है।',
  'एक छोटे लड़के के हाथ में एक मछली पकड़ने वाली छड़ी है और रेखा के अंत में एक मछली है और वह एक घेरे में इधर-उधर दौड़ रहा है।',
  'एक बच्चा चल रहा है।',
  'एक बच्चा पकड़ी गई मछली के साथ खेल रहा है।',
  'फिशिंग रॉड पर लटकी मछली के सामने एक लड़का दौड़ रहा है।',
  'मछली पकड़ने का खंभा पकड़े एक लड़का हलकों में दौड़ रहा है।',
  'एक बच्चा मछली से भाग रहा है।',
  'मछली पकड़ने के खंभे पर झूलती मछली को देखकर एक बच्चा भाग जाता है।',
  'एक बच्चा मछली से भाग रहा है।',
  'एक बच्चा मछली पकड़ने का पोल पकड़ रहा है।',
  'एक छोटा लड़का अभी-अभी पकड़ी गई मछली से दूर भाग रहा है।',
  'मछली पकड़ने वाली छड़ी के एक छोर पर मछली को चकमा देते हुए एक छोटा बच्चा छड़ी को घुमाते हुए, छड़ी को गिराकर भाग जाता है।',
  'एक छोटा बच्चा उस मछली से डरता 

In [26]:
testing_hindi_label=json.dumps(y_data)

In [28]:
y_data

[{'caption': ['एक रसोइया कच्चे मुर्गे तैयार करता है।',
   'एक मुर्गे को सीज किया जा रहा है।',
   'एक आदमी तिरछे पूरे मुर्गे में नमक मिला रहा है।',
   'एक शख्स मुर्गे के शरीर पर ढेर सारा नमक लेप कर रहा है.',
   'एक आदमी चिकन बना रहा है।',
   'एक आदमी मुर्गे पर नमक डाल रहा है।',
   'एक आदमी एक कच्ची चिड़िया को सीज कर रहा है।',
   'एक आदमी कच्चे मुर्गे पर नमक लगा रहा है।',
   'एक आदमी कच्चे मुर्गे पर आटा छिड़क रहा है।',
   'एक आदमी मुर्गा बना रहा है',
   'एक आदमी अपना मांस तैयार करता है।',
   'एक आदमी एक पूरे पक्षी पर एक सामग्री छिड़कता है।',
   'खाना पकाने के लिए अभिनेता क्रिस्टोफर वॉकेन पोल्ट्री सीज़न करते हैं।',
   'क्रिस्टोफर वॉकेन चिकन पका रहे हैं',
   'क्रिस्टोफर वॉकन एक चिकन तैयार करता है।',
   'आदमी मुर्गे पर आटा डाल रहा है।',
   'आदमी चिकन मसाला कर रहा है।'],
  'id': 'ScdUht-pM6s_53_63.avi'},
 {'caption': ['एक मछली पकड़ने वाला एक लड़के का पीछा कर रहा है।',
   'एक छोटा बच्चा अपने हाथ में पकड़ी हुई छड़ी पर मछली से बचने की कोशिश में घेरे में इधर-उधर दौड़ रहा है, तभी वह पोल को गिरा द

In [31]:
json_object = json.dumps(y_data)

In [32]:
with open("testing_hindi_label.json", "w") as outfile:
    outfile.write(json_object)

In [ ]:
# # for i in hindi_captions:
# # test_hin = json.dumps(hindi_captions)

# from googletrans import Translator
# translator = Translator()

# hindi_captions=[]
# tuples={}
# TRAIN_LABEL_PATH = os.path.join('', 'testing_hindi_label.json')
# with open(TRAIN_LABEL_PATH) as data_file:    
#     y_data = json.load(data_file)
#     for i in y_data:
#       hindi_captions=[]
#       for j in i['caption']:
#         hindi_captions.append(translator.translate(j,  dest='hi').text)
#       i['caption']=hindi_captions
#       print(i['id']+"\n")

In [33]:
json_file = open('/content/gdrive/MyDrive/Colab Notebooks/IT401_Project/testing_hindi_label.json')
data = json.load(json_file)

data

[{'caption': ['एक रसोइया कच्चे मुर्गे तैयार करता है।',
   'एक मुर्गे को सीज किया जा रहा है।',
   'एक आदमी तिरछे पूरे मुर्गे में नमक मिला रहा है।',
   'एक शख्स मुर्गे के शरीर पर ढेर सारा नमक लेप कर रहा है.',
   'एक आदमी चिकन बना रहा है।',
   'एक आदमी मुर्गे पर नमक डाल रहा है।',
   'एक आदमी एक कच्ची चिड़िया को सीज कर रहा है।',
   'एक आदमी कच्चे मुर्गे पर नमक लगा रहा है।',
   'एक आदमी कच्चे मुर्गे पर आटा छिड़क रहा है।',
   'एक आदमी मुर्गा बना रहा है',
   'एक आदमी अपना मांस तैयार करता है।',
   'एक आदमी एक पूरे पक्षी पर एक सामग्री छिड़कता है।',
   'खाना पकाने के लिए अभिनेता क्रिस्टोफर वॉकेन पोल्ट्री सीज़न करते हैं।',
   'क्रिस्टोफर वॉकेन चिकन पका रहे हैं',
   'क्रिस्टोफर वॉकन एक चिकन तैयार करता है।',
   'आदमी मुर्गे पर आटा डाल रहा है।',
   'आदमी चिकन मसाला कर रहा है।'],
  'id': 'ScdUht-pM6s_53_63.avi'},
 {'caption': ['एक मछली पकड़ने वाला एक लड़के का पीछा कर रहा है।',
   'एक छोटा बच्चा अपने हाथ में पकड़ी हुई छड़ी पर मछली से बचने की कोशिश में घेरे में इधर-उधर दौड़ रहा है, तभी वह पोल को गिरा द

In [47]:
TRAIN_LABEL_PATH = os.path.join('', 'training_hindi_label.json')
with open(TRAIN_LABEL_PATH) as data_file:    
    z_data = json.load(data_file)

In [58]:
from googletrans import Translator
translator = Translator()

hindi_captions=[]
TRAIN_LABEL_PATH = os.path.join('', 'training_hindi_label.json')
with open(TRAIN_LABEL_PATH) as data_file:    
    z_data = json.load(data_file)
    for i in range(1450):
      hindi_captions=[]
      print(y_data[i]['id'])
      for j in y_data[i]['caption']:
        hindi_captions.append(translator.translate(j,  dest='hi').text)
      y_data[i]['caption']=hindi_captions

Li3umATsU0E_1_5.avi


In [50]:
y_data

[{'caption': ['एक महिला घोड़े के नीचे जाती है।',
   'एक महिला घोड़े के नीचे रेंगती है और उसे एक सरप्राइज मिलता है।',
   'एक लड़की घोड़े की पिछली टांगों के बीच से अपना सिर बाहर निकाल रही है जो उसके सिर पर थूकता है।',
   'एक महिला के सिर पर एक घोड़ा मल गया।',
   'एक घोड़ा एक महिला के सिर पर मलत्याग करता है क्योंकि वह आगे और पीछे के पैरों के बीच में आ जाती है और अपना सिर बाहर निकाल लेती है।',
   'एक महिला के सिर पर एक घोड़ा शौच कर रहा है।',
   'एक घोड़ा महिला पर वार करता है।',
   'एक घोड़ा महिला पर वार करता है।',
   'एक महिला को इसलिए शिकार बनाया गया क्योंकि वह घोड़े की पूंछ के सिरे के नीचे थी।',
   'एक महिला घोड़े के नीचे रेंगती है और जब वह अपना सिर घोड़ों के पिछले पैरों के बीच चिपकाती है तो घोड़ा उसके सिर पर मल त्याग देता है।',
   'एक महिला घोड़े की पीठ के नीचे जाती है और शिकार करती है।',
   'एक महिला घोड़े के नीचे जाती है।',
   'एक महिला घोड़े के नीचे रेंग रही है।',
   'एक महिला को घोड़े द्वारा कुचला जा रहा है।',
   'एक महिला घोड़े की टांगों के बीच चल रही है।',
   'एक महिला घोड़े के नी

In [65]:
json_object = json.dumps(y_data)

In [66]:
with open("training_hindi_label.json", "w") as outfile:
    outfile.write(json_object)

In [68]:
json_file = open('/content/gdrive/MyDrive/Colab Notebooks/IT401_Project/training_hindi_label.json')
data = json.load(json_file)

data

[{'caption': ['एक महिला घोड़े के नीचे जाती है।',
   'एक महिला घोड़े के नीचे रेंगती है और उसे एक सरप्राइज मिलता है।',
   'एक लड़की घोड़े की पिछली टांगों के बीच से अपना सिर बाहर निकाल रही है जो उसके सिर पर थूकता है।',
   'एक महिला के सिर पर एक घोड़ा मल गया।',
   'एक घोड़ा एक महिला के सिर पर मलत्याग करता है क्योंकि वह आगे और पीछे के पैरों के बीच में आ जाती है और अपना सिर बाहर निकाल लेती है।',
   'एक महिला के सिर पर एक घोड़ा शौच कर रहा है।',
   'एक घोड़ा महिला पर वार करता है।',
   'एक घोड़ा महिला पर वार करता है।',
   'एक महिला को इसलिए शिकार बनाया गया क्योंकि वह घोड़े की पूंछ के सिरे के नीचे थी।',
   'एक महिला घोड़े के नीचे रेंगती है और जब वह अपना सिर घोड़ों के पिछले पैरों के बीच चिपकाती है तो घोड़ा उसके सिर पर मल त्याग देता है।',
   'एक महिला घोड़े की पीठ के नीचे जाती है और शिकार करती है।',
   'एक महिला घोड़े के नीचे जाती है।',
   'एक महिला घोड़े के नीचे रेंग रही है।',
   'एक महिला को घोड़े द्वारा कुचला जा रहा है।',
   'एक महिला घोड़े की टांगों के बीच चल रही है।',
   'एक महिला घोड़े के नी